In [1]:
import numpy, matplotlib, time, copy
directory = '../data/'
file_paths = ['a_example.txt', 'b_read_on.txt', 'c_incunabula.txt','d_tough_choices.txt', 'e_so_many_books.txt', 'f_libraries_of_the_world.txt']

In [2]:
class Library():
    def __init__(self,index,N,T,M, book_ids: set):
        self.id = index
        self.size  = N
        self.signup_time = T
        self.books_per_day = M
        self.book_ids = book_ids
        
    def get_n_best_books(self,n, bookValues):
        result = [];
        k=0
        for i in range(len(self.book_ids)):
            if bookValues[self.book_ids[i]] != 0:
                result.append(self.book_ids[i])
                k+=1
                if k == n:
                    return tuple(result)
        return tuple(result)
    
    def __str__(self):
        return str(self.__class__) + ": " + str(self.__dict__)
        
        

def process_file(filePath):
    with open(directory+filePath,'r') as file:
        content = file.read().split('\n')[:-1];
        B,L,D = content[0].split()
        B,L,D = int(B),int(L),int(D)
    bookValues = [int(n) for n in content[1].split()]#tuple([int(n) for n in content[1].split()])
    libraries = []
    def book_sort(book):
        return bookValues[book]
    for i in range(L):
        N,T,M = content[2+2*i].split()
        N,T,M=int(N),int(T),int(M)
        book_ids = tuple(sorted([int(id) for id in content[2+2*i+1].split()], key = book_sort, reverse=True))
        libraries.append(Library(i,N,T,M,book_ids))
    return ((B,L,D), bookValues, libraries)

In [3]:
def check_solution(D, libraries):
    print("D ",D)
    days = 0
    prev_books = set()
    for library in libraries:
#         print("#################")
#         print("Library id", library.id)
#         print("signup", library.signup_time)
#         print("Books per day", library.books_per_day)
#         print("all books", len(library.book_ids))
# #         print("##############")
        days+=library.signup_time
        if len(library.book_ids) > (D-days)*library.books_per_day:
            print("what", len(library.book_ids), (D-days)*library.books_per_day)
#         elif len(library.book_ids) < (D-days)*library.books_per_day:
#             print("warning", len(library.book_ids), (D-days)*library.books_per_day)
        assert(not any([(book in prev_books) for book in library.book_ids]))
        prev_books.update(library.book_ids)
    assert(days <= D)

In [4]:

def get_score(file_path):
    (B,L,D),bookValues, libraries = process_file(file_path)
    unmodified_book_values = copy.copy(bookValues)
    chosen_libraries = []
    day = 0
    def book_sort(book):
        return bookValues[book]
    def library_score(lib):
        delta_time = D - lib.signup_time
        n_best_books = lib.get_n_best_books(delta_time*lib.signup_time, bookValues)
        sum_of_best_book_scores = sum([bookValues[book] for book in n_best_books])
        return sum_of_best_book_scores/lib.signup_time
    
    while libraries:
        library_scores = [library_score(lib) for lib in libraries]
        next_library_index = library_scores.index(max(library_scores))
        next_library = libraries[next_library_index]
        day+=next_library.signup_time
        if day >= D:
            break
        next_library.book_ids = next_library.get_n_best_books((D-day)*next_library.books_per_day, bookValues)
        for book_id in next_library.book_ids:
            bookValues[book_id] = 0
        chosen_libraries.append(next_library)
        libraries.pop(next_library_index)
        
    print(len(chosen_libraries))
    score = 0
    for library in chosen_libraries:
        for idk in library.book_ids:
            score+=unmodified_book_values[idk]
    check_solution(D, chosen_libraries)
    return score
sum_score = 0
for file_path in file_paths:
    print(file_path)
    %time sum_score+=get_score(file_path)
print("SUM SCORE", sum_score)

a_example.txt
2
D  7
CPU times: user 1.31 ms, sys: 740 µs, total: 2.05 ms
Wall time: 1.21 ms
b_read_on.txt
90
D  1000
CPU times: user 1.65 s, sys: 3.61 ms, total: 1.65 s
Wall time: 1.66 s
c_incunabula.txt
1284
D  100000
CPU times: user 1min 16s, sys: 2.96 ms, total: 1min 16s
Wall time: 1min 16s
d_tough_choices.txt
15000
D  30001
CPU times: user 15min 21s, sys: 243 ms, total: 15min 21s
Wall time: 15min 21s
e_so_many_books.txt
131
D  200
CPU times: user 17.8 s, sys: 7.99 ms, total: 17.8 s
Wall time: 17.8 s
f_libraries_of_the_world.txt
17
D  700
CPU times: user 3.44 s, sys: 16 ms, total: 3.46 s
Wall time: 3.46 s
SUM SCORE 26344324


In [5]:
def get_score(file_path):
    (B,L,D),bookValues, libraries = process_file(file_path)
    unmodified_book_values = copy.copy(bookValues)
    day = 0
    def book_sort(book):
        return bookValues[book]
    def library_score(lib):
        delta_time = D - lib.signup_time
        n_best_books = lib.get_n_best_books(delta_time*lib.signup_time, bookValues)
        sum_of_best_book_scores = sum([bookValues[book] for book in n_best_books])
        return sum_of_best_book_scores/lib.signup_time
#         return sum(sorted(lib.book_ids,key = book_sort, reverse=True)[:min(delta_time*lib.books_per_day,lib.size)])/lib.signup_time
    print(time.time())
    sorted_libraries = sorted(libraries,key=library_score, reverse=True)
    print("Sorted", [lib.id for lib in sorted_libraries])
    print(time.time())
    it=0;
    while it < len(sorted_libraries):
        next_library = sorted_libraries[it]
        print(next_library)
        day+=next_library.signup_time
        if day>=D:
            break
        print("oop")
        print("ejejej",D,day, D-day)
        print(len(next_library.book_ids), (D-day)*next_library.books_per_day)
        next_library.book_ids = next_library.get_n_best_books((D-day)*next_library.books_per_day, bookValues)
        print(len(next_library.book_ids))
        for book_id in next_library.book_ids:
            bookValues[book_id] = 0
        sorted_libraries[it] = next_library
        it+=1
    print(time.time())
    score = 0
    for i in range(0,it):
        for idk in sorted_libraries[i].book_ids:
            score+=unmodified_book_values[idk]
    print("SCORE ",score)
    
    check_solution(D, sorted_libraries[:it])
    return score
sum_scores = 0
for file_path in file_paths:
    print(file_path)
    %time sum_scores +=get_score(file_path)
print("SUM SCORES", sum_scores)

a_example.txt
1609023209.8410423
Sorted [0, 1]
1609023209.8414857
<class '__main__.Library'>: {'id': 0, 'size': 5, 'signup_time': 2, 'books_per_day': 2, 'book_ids': (3, 4, 2, 1, 0)}
oop
ejejej 7 2 5
5 10
5
<class '__main__.Library'>: {'id': 1, 'size': 4, 'signup_time': 3, 'books_per_day': 1, 'book_ids': (3, 5, 2, 0)}
oop
ejejej 7 5 2
4 2
1
1609023209.8419428
SCORE  21
D  7
CPU times: user 1.78 ms, sys: 1e+03 ns, total: 1.78 ms
Wall time: 1.23 ms
b_read_on.txt
1609023209.9007795
Sorted [38, 92, 27, 29, 48, 73, 77, 11, 34, 66, 88, 21, 32, 65, 75, 82, 18, 37, 57, 76, 2, 9, 22, 62, 14, 16, 31, 89, 13, 42, 46, 52, 53, 67, 69, 79, 84, 36, 40, 43, 55, 56, 61, 86, 90, 6, 30, 64, 78, 91, 59, 99, 7, 15, 58, 83, 3, 4, 12, 20, 28, 41, 45, 63, 81, 87, 5, 19, 23, 26, 85, 94, 44, 47, 50, 72, 74, 93, 8, 25, 33, 39, 70, 71, 80, 98, 54, 68, 0, 1, 10, 17, 24, 35, 49, 51, 60, 95, 96, 97]
1609023209.9315255
<class '__main__.Library'>: {'id': 38, 'size': 1000, 'signup_time': 1, 'books_per_day': 1, 'book_ids

223
<class '__main__.Library'>: {'id': 25, 'size': 1000, 'signup_time': 18, 'books_per_day': 1, 'book_ids': (25000, 25001, 25002, 25003, 25004, 25005, 25006, 25007, 25008, 25009, 25010, 25011, 25012, 25013, 25014, 25015, 25016, 25017, 25018, 25019, 25020, 25021, 25022, 25023, 25024, 25025, 25026, 25027, 25028, 25029, 25030, 25031, 25032, 25033, 25034, 25035, 25036, 25037, 25038, 25039, 25040, 25041, 25042, 25043, 25044, 25045, 25046, 25047, 25048, 25049, 25050, 25051, 25052, 25053, 25054, 25055, 25056, 25057, 25058, 25059, 25060, 25061, 25062, 25063, 25064, 25065, 25066, 25067, 25068, 25069, 25070, 25071, 25072, 25073, 25074, 25075, 25076, 25077, 25078, 25079, 25080, 25081, 25082, 25083, 25084, 25085, 25086, 25087, 25088, 25089, 25090, 25091, 25092, 25093, 25094, 25095, 25096, 25097, 25098, 25099, 25100, 25101, 25102, 25103, 25104, 25105, 25106, 25107, 25108, 25109, 25110, 25111, 25112, 25113, 25114, 25115, 25116, 25117, 25118, 25119, 25120, 25121, 25122, 25123, 25124, 25125, 25126, 25

1609023210.1867285
Sorted [1949, 8696, 4871, 6550, 4705, 9772, 8384, 2297, 7327, 2610, 5724, 3428, 8530, 6241, 5523, 8617, 8738, 1634, 8917, 3953, 6897, 1864, 4758, 8728, 53, 9829, 7989, 8691, 1045, 4193, 2359, 7281, 18, 8149, 9255, 1760, 627, 3938, 349, 8791, 7491, 9447, 5134, 1161, 2380, 9092, 177, 650, 9128, 1023, 111, 6871, 198, 5771, 8887, 6644, 7819, 2006, 2882, 5348, 8758, 8181, 7791, 2346, 661, 7358, 8490, 122, 8279, 7984, 4074, 6754, 5804, 806, 4460, 2732, 5020, 7709, 7305, 9927, 416, 9855, 5339, 1549, 479, 1653, 3679, 1349, 8005, 1283, 6063, 2754, 4059, 1448, 5707, 4138, 5023, 1004, 587, 2415, 1737, 6441, 5263, 6338, 6636, 555, 6202, 6979, 399, 9566, 9053, 8226, 4592, 7511, 2652, 2737, 8050, 6213, 2394, 1348, 752, 1356, 7021, 2863, 5064, 2144, 906, 1800, 2939, 5311, 4112, 1559, 4439, 7368, 7075, 4924, 8283, 3546, 2942, 6997, 6129, 3124, 6772, 9918, 1296, 6342, 8795, 2044, 6313, 751, 6953, 4589, 5853, 220, 8124, 9027, 115, 2919, 7201, 9367, 2143, 5219, 6253, 8505, 9316, 9610, 

ejejej 100000 2554 97446
12 2607167730
11
<class '__main__.Library'>: {'id': 3124, 'size': 14, 'signup_time': 21, 'books_per_day': 13313, 'book_ids': (99244, 31431, 99456, 1683, 57835, 79809, 42065, 11593, 4303, 89360, 88888, 45851, 24803, 7441)}
oop
ejejej 100000 2575 97425
14 1297019025
14
<class '__main__.Library'>: {'id': 6772, 'size': 13, 'signup_time': 23, 'books_per_day': 16180, 'book_ids': (95671, 19919, 86445, 24112, 75938, 62509, 23500, 45113, 88834, 90050, 95512, 46842, 68161)}
oop
ejejej 100000 2598 97402
13 1575964360
13
<class '__main__.Library'>: {'id': 9918, 'size': 10, 'signup_time': 18, 'books_per_day': 49105, 'book_ids': (63551, 71772, 47523, 14457, 27484, 83949, 61821, 79933, 49584, 31825)}
oop
ejejej 100000 2616 97384
10 4782041320
10
<class '__main__.Library'>: {'id': 1296, 'size': 11, 'signup_time': 18, 'books_per_day': 11319, 'book_ids': (80466, 19174, 88340, 88752, 28937, 9005, 26826, 95303, 84642, 45191, 95991)}
oop
ejejej 100000 2634 97366
11 1102085754
11
<c

18
<class '__main__.Library'>: {'id': 3854, 'size': 19, 'signup_time': 40, 'books_per_day': 85692, 'book_ids': (2245, 69562, 45850, 55034, 6534, 36681, 23466, 80787, 84046, 23882, 76913, 94929, 20817, 92790, 32246, 28893, 28622, 27739, 34562)}
oop
ejejej 100000 4174 95826
19 8211521592
18
<class '__main__.Library'>: {'id': 7731, 'size': 18, 'signup_time': 38, 'books_per_day': 35640, 'book_ids': (74564, 70586, 71930, 54980, 31608, 22107, 6507, 32855, 36559, 30295, 4279, 72130, 52336, 19993, 53230, 3217, 89097, 63158)}
oop
ejejej 100000 4212 95788
18 3413884320
18
<class '__main__.Library'>: {'id': 7956, 'size': 16, 'signup_time': 31, 'books_per_day': 4482, 'book_ids': (23650, 83790, 34990, 86621, 25103, 2365, 19498, 11082, 59305, 43098, 99270, 76310, 39793, 8361, 89710, 91358)}
oop
ejejej 100000 4243 95757
16 429182874
16
<class '__main__.Library'>: {'id': 92, 'size': 10, 'signup_time': 21, 'books_per_day': 71484, 'book_ids': (73669, 87154, 33545, 20672, 9131, 37274, 57354, 42710, 23932

...

7 243
0
<class '__main__.Library'>: {'id': 4088, 'size': 7, 'signup_time': 2, 'books_per_day': 1, 'book_ids': (24646, 14891, 17713, 24647, 24648, 24649, 24650)}
oop
ejejej 30001 29760 241
7 241
1
<class '__main__.Library'>: {'id': 4092, 'size': 7, 'signup_time': 2, 'books_per_day': 1, 'book_ids': (24666, 22377, 24667, 24668, 24669, 17565, 24670)}
oop
ejejej 30001 29762 239
7 239
2
<class '__main__.Library'>: {'id': 4097, 'size': 7, 'signup_time': 2, 'books_per_day': 1, 'book_ids': (24687, 24695, 19676, 24696, 24697, 24698, 24699)}
oop
ejejej 30001 29764 237
7 237
0
<class '__main__.Library'>: {'id': 4100, 'size': 7, 'signup_time': 2, 'books_per_day': 1, 'book_ids': (24711, 24712, 24713, 17965, 24714, 14852, 24715)}
oop
ejejej 30001 29766 235
7 235
2
<class '__main__.Library'>: {'id': 4103, 'size': 7, 'signup_time': 2, 'books_per_day': 1, 'book_ids': (24723, 24729, 6765, 9133, 24730, 15451, 24731)}
oop
ejejej 30001 29768 233
7 233
0
<class '__main__.Library'>: {'id': 4109, 'size': 7, 's

1609023223.1043396
Sorted [600, 594, 522, 972, 602, 717, 100, 209, 178, 597, 808, 61, 715, 157, 393, 72, 466, 59, 690, 390, 708, 933, 813, 4, 37, 952, 495, 626, 478, 902, 854, 506, 607, 491, 87, 693, 736, 270, 476, 244, 387, 241, 343, 158, 27, 125, 23, 970, 959, 779, 665, 82, 350, 700, 669, 239, 232, 555, 148, 388, 69, 577, 556, 828, 852, 995, 691, 117, 894, 520, 678, 335, 589, 993, 848, 830, 969, 971, 304, 142, 639, 359, 630, 320, 512, 795, 793, 267, 150, 944, 60, 737, 455, 621, 633, 366, 268, 410, 587, 462, 411, 606, 443, 583, 834, 220, 205, 191, 245, 563, 210, 844, 0, 216, 112, 373, 566, 780, 962, 772, 815, 105, 314, 575, 447, 798, 988, 179, 794, 403, 288, 45, 581, 461, 76, 266, 431, 653, 64, 504, 160, 140, 400, 20, 534, 821, 510, 356, 674, 14, 104, 71, 535, 333, 434, 475, 623, 389, 336, 479, 809, 358, 339, 237, 316, 996, 586, 325, 635, 973, 603, 517, 838, 62, 845, 39, 234, 983, 782, 927, 911, 511, 503, 457, 273, 718, 963, 753, 21, 428, 80, 666, 197, 536, 676, 869, 129, 570, 383, 10

133
<class '__main__.Library'>: {'id': 556, 'size': 863, 'signup_time': 2, 'books_per_day': 1, 'book_ids': (32626, 28452, 81068, 828, 78066, 35361, 80962, 82273, 94639, 37492, 30711, 73545, 10691, 42978, 92441, 25066, 96893, 70879, 89945, 98802, 74356, 67096, 70021, 19132, 72945, 76452, 60088, 83078, 29698, 26842, 45587, 44031, 51204, 97709, 38830, 36694, 20059, 86809, 88724, 18626, 86830, 9928, 90250, 47984, 63000, 1482, 18286, 61470, 16660, 64433, 75558, 13329, 76743, 10140, 18949, 68238, 14255, 34763, 92199, 23548, 40975, 55343, 22719, 62017, 77783, 21502, 70649, 36426, 55048, 3208, 32879, 15965, 61605, 91303, 74901, 87950, 3158, 11274, 91447, 31465, 5530, 12898, 70347, 87244, 73124, 62333, 77532, 47427, 36133, 60526, 93736, 66513, 74144, 36352, 62140, 87863, 23005, 68865, 55643, 8471, 12440, 21694, 16633, 43959, 30517, 98340, 58666, 57083, 77669, 77257, 90851, 96535, 11620, 72595, 41846, 25629, 72973, 76390, 61167, 67812, 74592, 7279, 62845, 64764, 79091, 221, 40142, 17355, 40512, 

1609023223.6868086
Sorted [204, 210, 694, 719, 595, 774, 901, 618, 369, 422, 312, 622, 672, 828, 209, 454, 147, 563, 515, 31, 247, 902, 869, 21, 319, 112, 813, 230, 387, 43, 692, 847, 219, 497, 987, 481, 201, 457, 273, 156, 527, 949, 893, 927, 330, 142, 993, 352, 944, 86, 420, 723, 969, 390, 895, 261, 517, 970, 503, 99, 445, 732, 23, 646, 880, 106, 75, 773, 952, 624, 948, 881, 211, 221, 37, 11, 108, 938, 789, 837, 385, 573, 502, 665, 105, 281, 344, 128, 188, 706, 258, 288, 81, 839, 400, 242, 98, 425, 18, 928, 304, 193, 194, 819, 500, 664, 262, 508, 373, 468, 739, 663, 226, 615, 578, 449, 745, 16, 166, 743, 438, 136, 939, 197, 724, 584, 941, 419, 57, 78, 657, 759, 126, 431, 94, 248, 923, 516, 168, 570, 467, 636, 380, 865, 909, 113, 700, 551, 244, 628, 51, 541, 159, 545, 62, 296, 30, 49, 649, 561, 524, 499, 566, 741, 217, 198, 365, 687, 350, 678, 440, 40, 764, 681, 604, 795, 270, 602, 621, 540, 114, 415, 834, 937, 1, 150, 979, 402, 906, 138, 54, 0, 266, 399, 36, 742, 806, 781, 823, 610, 

574 440
440
<class '__main__.Library'>: {'id': 147, 'size': 906, 'signup_time': 51, 'books_per_day': 5, 'book_ids': (9532, 1430, 63835, 18438, 57065, 79267, 65988, 81130, 16157, 82326, 19216, 52313, 81638, 17391, 71295, 96232, 83647, 9958, 59768, 19805, 13991, 83985, 8215, 99936, 94892, 11388, 38471, 66250, 79729, 9242, 18040, 70314, 87297, 82083, 8622, 69758, 70126, 94300, 29926, 34490, 11614, 44375, 17842, 23082, 70500, 81069, 88424, 44387, 52114, 77929, 14759, 62695, 33171, 79978, 23390, 94854, 54791, 34244, 78410, 67471, 84083, 70278, 11435, 28605, 76788, 30117, 99508, 98666, 87565, 10836, 7870, 56321, 61023, 40515, 71180, 82215, 90446, 83856, 16047, 62301, 10832, 14182, 35958, 38149, 13083, 12585, 44987, 6821, 7383, 36594, 82723, 89058, 12108, 38305, 58436, 35929, 98710, 99966, 84331, 13757, 71257, 42719, 58782, 93889, 48236, 70894, 9736, 68495, 14585, 56462, 27556, 69029, 81155, 92423, 52584, 87587, 69353, 56570, 80265, 62847, 38677, 44769, 29758, 77335, 53423, 7823, 16641, 53535